L'installation [Elasticité dynamique](https://github.com/laurentperrinet/elasticite) agit comme un filtre et génère de nouveaux espaces démultipliés, comme un empilement quasi infini d'horizons. Par principe de réflexion, la pièce absorbe l'image de l'environnement et accumule les points de vue ; le mouvement permanent requalifie continuellement ce qui est regardé et entendu. 

Ce post étudie la connection entre le raspberry π (qui fait tourner les simulations) et les arduino (qui commandent les moteurs).

<!-- TEASER_END -->

In [1]:
%load_ext autoreload
%autoreload 2
import numpy as np

1. sharing internet on the laocal machine

````
    ifconfig
````

2. scanning the local network to find the raspberry π

````
    nmap -T4 -sP 192.168.2.0/24
````

3. what I used to clone the repository on the π

````
  686  pip install pyserial
  687  vim .ssh/id_rsa.pub
  688  vim .ssh/id_rsa
  689  chmod 0600 .ssh/id_rsa
  690  git clone git@git.framasoft.org:laurentperrinet/elasticte.git
  691  cd elasticte/
  692  ls
  693  cat scenario_line_contraint.py
  694  python scenario_line_contraint.py  serial
  695  pip install -e .
  696  pip install --user -e .
  697  python scenario_line_contraint.py  serial
````

4. starting 

````

⇒  ssh pi@192.168.2.3

Linux pielastic 3.18.7-v7+ #755 SMP PREEMPT Thu Feb 12 17:20:48 GMT 2015 armv7l

pi@pielastic ~ $ cd elasticte/

pi@pielastic ~/elasticte $ git pull # to update the code
Already up-to-date.

pi@pielastic ~/elasticte $ python scenario_line_contraint.py serial

````


## coordonées absolues

Prenons un cas  simple avec 12 pas possible et calculons en fonction de la position actuelle et de la position désirée la commande à envoyer aux moteurs

In [2]:
nb_pas = 12
position_present = 6
position_desired = 4

d_position = (position_desired - position_present + nb_pas//2 ) % nb_pas - nb_pas//2

print (d_position)

position_present = (position_present + d_position ) % nb_pas

print (position_present)


-2
4


on vérifie que ça marche pour toute une série de positions désirées et qu'on évite le demi tour:

In [3]:
nb_pas = 12
position_present = 2
position_desired = np.arange(nb_pas)

d_position = (position_desired - position_present + nb_pas//2 ) % nb_pas - nb_pas//2

print (d_position)

position_present = (position_present + d_position ) % nb_pas

print (position_present)


[-2 -1  0  1  2  3  4  5 -6 -5 -4 -3]
[ 0  1  2  3  4  5  6  7  8  9 10 11]


on vérifie aussi que ça marche pour toute une série de positions initiales et qu'on évite le demi tour:

In [4]:
nb_pas = 12
position_present = np.arange(nb_pas)
position_desired = 8

d_position = (position_desired - position_present + nb_pas//2 ) % nb_pas - nb_pas//2

print (d_position)

position_present = (position_present + d_position ) % nb_pas

print (position_present)


[-4 -5 -6  5  4  3  2  1  0 -1 -2 -3]
[8 8 8 8 8 8 8 8 8 8 8 8]


### arduino

coordonnées moteur + engrenage:
 - 1.8 deg par pas (soit 200 pas par tour) x 32 divisions de pas = 
 - demultiplication : pignon1= 14 dents, pignon2 = 60 dents


In [5]:
n_pas = 200. * 32. * 60 / 14
print(n_pas)

27428.571428571428


Donc, on a un nombre même pas entier mais c'est pas grave. C'est le nombre de pas à faire pour le moteur pour faire faire un tour à la lame. Dans un premier temps, on va considérer ce cercle comme des entiers entre 0 et n_pas. ça devrait pouvoir être envoyé sans probleme a chaque arduino comme un int16 (à vérifier - si on a de la marge, on peut faire un truc plus précis): 

In [6]:
2**16

65536

L'algo sur le arduino doit donc avoir cette partie pour convertir une donnée absolue reçue en donnée relative à envoyer aux moteurs:

In [7]:
nb_pas = 27428

position_present = 27424
position_desired = 4 # recu avec la lecture sur le port série

# quand on reçoit une valeur absolue on calcule
d_position = (position_desired - position_present + nb_pas//2 ) % nb_pas - nb_pas//2

# on envoie d_position aux moteurs

# on met à jour la position du moteur
position_present = (position_present + d_position ) % nb_pas

print(d_position, position_present)

8 4


## git


In [8]:
!git s
#!git add 2015-10-27\ élasticité\ r*

?? __temp_ipython__.png
?? anim.gif


In [11]:
!git commit -am' on connecte le π + coordonnées absolues'

[master e968673]  on connecte le π + coordonnées absolues
 1 file changed, 12 insertions(+), 14 deletions(-)


In [12]:
! git push

Counting objects: 4, done.
Delta compression using up to 4 threads.
Compressing objects: 100% (4/4), done.
Writing objects: 100% (4/4), 636 bytes | 0 bytes/s, done.
Total 4 (delta 3), reused 0 (delta 0)
To git@git.framasoft.org:laurentperrinet/elasticte.git
   9dd54ff..e968673  master -> master
